In [152]:
%matplotlib inline
import matplotlib
import seaborn as sns
matplotlib.rcParams['savefig.dpi'] = 144

In [153]:
from static_grader import grader

# PW Miniproject
## Introduction

The objective of this miniproject is to exercise your ability to use basic Python data structures, define functions, and control program flow. We will be using these concepts to perform some fundamental data wrangling tasks such as joining data sets together, splitting data into groups, and aggregating data into summary statistics.
**Please do not use `pandas` or `numpy` to answer these questions.**

We will be working with medical data from the British NHS on prescription drugs. Since this is real data, it contains many ambiguities that we will need to confront in our analysis. This is commonplace in data science, and is one of the lessons you will learn in this miniproject.

## Downloading the data

We first need to download the data we'll be using from Amazon S3:

In [4]:
%%bash
mkdir pw-data
wget http://dataincubator-wqu.s3.amazonaws.com/pwdata/201701scripts_sample.json.gz -nc -P ./pw-data
wget http://dataincubator-wqu.s3.amazonaws.com/pwdata/practices.json.gz -nc -P ./pw-data

mkdir: cannot create directory ‘pw-data’: File exists
File ‘./pw-data/201701scripts_sample.json.gz’ already there; not retrieving.

File ‘./pw-data/practices.json.gz’ already there; not retrieving.



## Loading the data

The first step of the project is to read in the data. We will discuss reading and writing various kinds of files later in the course, but the code below should get you started.

In [6]:
import gzip
import simplejson as json

In [4]:
with gzip.open('./pw-data/201701scripts_sample.json.gz', 'rb') as f:
    scripts = json.load(f)

with gzip.open('./pw-data/practices.json.gz', 'rb') as f:
    practices = json.load(f)

This data set comes from Britain's National Health Service. The `scripts` variable is a list of prescriptions issued by NHS doctors. Each prescription is represented by a dictionary with various data fields: `'practice'`, `'bnf_code'`, `'bnf_name'`, `'quantity'`, `'items'`, `'nic'`, and `'act_cost'`. 

In [5]:
scripts[:2]

[{'bnf_code': '0101010G0AAABAB',
  'items': 2,
  'practice': 'N81013',
  'bnf_name': 'Co-Magaldrox_Susp 195mg/220mg/5ml S/F',
  'nic': 5.98,
  'act_cost': 5.56,
  'quantity': 1000},
 {'bnf_code': '0101021B0AAAHAH',
  'items': 1,
  'practice': 'N81013',
  'bnf_name': 'Alginate_Raft-Forming Oral Susp S/F',
  'nic': 1.95,
  'act_cost': 1.82,
  'quantity': 500}]

A [glossary of terms](http://webarchive.nationalarchives.gov.uk/20180328130852tf_/http://content.digital.nhs.uk/media/10686/Download-glossary-of-terms-for-GP-prescribing---presentation-level/pdf/PLP_Presentation_Level_Glossary_April_2015.pdf/) and [FAQ](http://webarchive.nationalarchives.gov.uk/20180328130852tf_/http://content.digital.nhs.uk/media/10048/FAQs-Practice-Level-Prescribingpdf/pdf/PLP_FAQs_April_2015.pdf/) is available from the NHS regarding the data. Below we supply a data dictionary briefly describing what these fields mean.

| Data field |Description|
|:----------:|-----------|
|`'practice'`|Code designating the medical practice issuing the prescription|
|`'bnf_code'`|British National Formulary drug code|
|`'bnf_name'`|British National Formulary drug name|
|`'quantity'`|Number of capsules/quantity of liquid/grams of powder prescribed|
| `'items'`  |Number of refills (e.g. if `'quantity'` is 30 capsules, 3 `'items'` means 3 bottles of 30 capsules)|
|  `'nic'`   |Net ingredient cost|
|`'act_cost'`|Total cost including containers, fees, and discounts|

The `practices` variable is a list of member medical practices of the NHS. Each practice is represented by a dictionary containing identifying information for the medical practice. Most of the data fields are self-explanatory. Notice the values in the `'code'` field of `practices` match the values in the `'practice'` field of `scripts`.

In [6]:
practices[:2]

[{'code': 'A81001',
  'name': 'THE DENSHAM SURGERY',
  'addr_1': 'THE HEALTH CENTRE',
  'addr_2': 'LAWSON STREET',
  'borough': 'STOCKTON ON TEES',
  'village': 'CLEVELAND',
  'post_code': 'TS18 1HU'},
 {'code': 'A81002',
  'name': 'QUEENS PARK MEDICAL CENTRE',
  'addr_1': 'QUEENS PARK MEDICAL CTR',
  'addr_2': 'FARRER STREET',
  'borough': 'STOCKTON ON TEES',
  'village': 'CLEVELAND',
  'post_code': 'TS18 2AW'}]

In the following questions we will ask you to explore this data set. You may need to combine pieces of the data set together in order to answer some questions. Not every element of the data set will be used in answering the questions.

## Question 1: summary_statistics

Our beneficiary data (`scripts`) contains quantitative data on the number of items dispensed (`'items'`), the total quantity of item dispensed (`'quantity'`), the net cost of the ingredients (`'nic'`), and the actual cost to the patient (`'act_cost'`). Whenever working with a new data set, it can be useful to calculate summary statistics to develop a feeling for the volume and character of the data. This makes it easier to spot trends and significant features during further stages of analysis.

Calculate the sum, mean, standard deviation, and quartile statistics for each of these quantities. Format your results for each quantity as a list: `[sum, mean, standard deviation, 1st quartile, median, 3rd quartile]`. We'll create a `tuple` with these lists for each quantity as a final result.

In [ ]:

def describe(key):

    total = 0
    avg = 0
    s = 0
    q25 = 0
    med = 0
    q75 = 0

    return (total, avg, s, q25, med, q75)

In [ ]:
summary = [('items', describe('items')),
           ('quantity', describe('quantity')),
           ('nic', describe('nic')),
           ('act_cost', describe('act_cost'))]

In [ ]:
grader.score.pw__summary_statistics(summary)

## Question 2: most_common_item

Often we are not interested only in how the data is distributed in our entire data set, but within particular groups -- for example, how many items of each drug (i.e. `'bnf_name'`) were prescribed? Calculate the total items prescribed for each `'bnf_name'`. What is the most commonly prescribed `'bnf_name'` in our data?

To calculate this, we first need to split our data set into groups corresponding with the different values of `'bnf_name'`. Then we can sum the number of items dispensed within in each group. Finally we can find the largest sum.

We'll use `'bnf_name'` to construct our groups. You should have *5619* unique values for `'bnf_name'`.

In [ ]:
bnf_names = ...
assert(len(bnf_names) == 5619)

We want to construct "groups" identified by `'bnf_name'`, where each group is a collection of prescriptions (i.e. dictionaries from `scripts`). We'll construct a dictionary called `groups`, using `bnf_names` as the keys. We'll represent a group with a `list`, since we can easily append new members to the group. To split our `scripts` into groups by `'bnf_name'`, we should iterate over `scripts`, appending prescription dictionaries to each group as we encounter them.

In [ ]:
groups = {name: [] for name in bnf_names}
for script in scripts:
    # INSERT ...

Now that we've constructed our groups we should sum up `'items'` in each group and find the `'bnf_name'` with the largest sum. The result, `max_item`, should have the form `[(bnf_name, item total)]`, e.g. `[('Foobar', 2000)]`.

In [ ]:
max_item = [("", 0)]

**TIP:** If you are getting an error from the grader below, please make sure your answer conforms to the correct format of `[(bnf_name, item total)]`.

In [ ]:
grader.score.pw__most_common_item(max_item)

**Challenge:** Write a function that constructs groups as we did above. The function should accept a list of dictionaries (e.g. `scripts` or `practices`) and a tuple of fields to `groupby` (e.g. `('bnf_name')` or `('bnf_name', 'post_code')`) and returns a dictionary of groups. The following questions will require you to aggregate data in groups, so this could be a useful function for the rest of the miniproject.

In [ ]:
def group_by_field(data, fields):
    groups = {}
    return groups

In [ ]:
groups = group_by_field(scripts, ('bnf_name',))
test_max_item = ...

assert test_max_item == max_item

## Question 3: postal_totals

Our data set is broken up among different files. This is typical for tabular data to reduce redundancy. Each table typically contains data about a particular type of event, processes, or physical object. Data on prescriptions and medical practices are in separate files in our case. If we want to find the total items prescribed in each postal code, we will have to _join_ our prescription data (`scripts`) to our clinic data (`practices`).

Find the total items prescribed in each postal code, representing the results as a list of tuples `(post code, total items prescribed)`. Sort your results ascending alphabetically by post code and take only results from the first 100 post codes. Only include post codes if there is at least one prescription from a practice in that post code.

**NOTE:** Some practices have multiple postal codes associated with them. Use the alphabetically first postal code.

We can join `scripts` and `practices` based on the fact that `'practice'` in `scripts` matches `'code'` in `practices`. However, we must first deal with the repeated values of `'code'` in `practices`. We want the alphabetically first postal codes.

In [23]:
sample = practices[:50]

In [5]:
def _redundcy(data, fields):
    print("_redundcy")
    unique_dics_list = _dic_unique_entry(data, fields)
    groups = {}
    for f in fields:
        g = {}
        for e in unique_dics_list[f]:
            g[e] = _index_list(e, data[f])
        groups[f] = g
    return groups
    
def _index_list(item, my_list):
#    print("_index_list")
    """Return index list for a given key on list"""
    return [index for index, event in enumerate(my_list) if event == item ]

def _index_to_value(index_list,my_list):
#    print("_index_to_value")
    return [my_list[i] for i in index_list]

def _unique_entry(my_list):
    print("_unique_entry")
    return list(sorted(set(my_list)))

def _dic_unique_entry(data, fields):
    print("_dic_unique_entry")
    unq = {}
    for f in fields:
        unq[f] = _unique_entry(data[f])
    return unq
    
def _set_difference(data, fields):
    print("_set_difference")
    keys = set(data.keys())
    fields = set(fields)
    fields.add('index')
    d = keys.difference(fields)
    return d

def _get_keys(lst):
    print("_get_keys")
    return [key for key in lst[0].keys()] 
    
def _json_to_data(json):
    print("_json_to_data")
    data_dic = {}
    data_keys = _get_keys(json)
    """Make EMPTY LIST of Data Dictionary of each Keys"""
    for key in data_keys:
        data_dic[key] = []
    """Add All the Data to Specific key by opening each entry in First Loop & add on data_dic in next loop"""
    for entry in json:
        for key in data_keys:
            data_dic[key].append(entry[key]) 
    data_dic['index'] = list(range(0,len(data_dic[data_keys[0]])))
    return data_dic

def _index_dic(data,keys):
    print("_index_dic")
    i_dict = {}
    for i in data['index']:
        l = []
        for key in keys:
            l.append(data[key][i])
        i_dict[i] = l
    return i_dict

def _dic_to_index(groups,idx):
    print("-dic_to_index")
    ng = {}
    for f in groups.keys():
        for key in groups[f].keys():
            ng[key] = _index_to_value(groups[f][key],idx)
    return ng

def group_by_field(json, fields,k):
    print("group_by_field")
    data = _json_to_data(json)
    keys = list(_set_difference(data, fields))
    keys = k
    groups = _redundcy(data, fields)
    idx = _index_dic(data,keys)
    return _dic_to_index(groups,idx)

In [8]:
#sample = practices[:50]
"""Run to check"""
x = group_by_field(practices,('code',),['post_code'])
x['K82019']

group_by_field
_json_to_data
_get_keys
_set_difference
_redundcy
_dic_unique_entry
_unique_entry
_index_dic
-dic_to_index


[['HP21 8TR'], ['MK6 2LR']]

In [14]:
def list_tuple(dicts):
    d = {}
    for i in dicts.keys():
        d[i] = sorted(dicts[i])[0][0]
    return d

practice_postal = list_tuple(x)
practice_postal['K82019']

'HP21 8TR'

In [ ]:

for practice in practices:
    if practice['code'] in practice_postal:
        practice_postal[practice['code']] = ...
    else:
        practice_postal[practice['code']] = ...

**Challenge:** This is an aggregation of the practice data grouped by practice codes. Write an alternative implementation of the above cell using the `group_by_field` function you defined previously.

In [15]:
assert practice_postal['K82019'] == 'HP21 8TR'

**Challenge:** This is an aggregation of the practice data grouped by practice codes. Write an alternative implementation of the above cell using the `group_by_field` function you defined previously.

In [96]:
assert practice_postal['K82019'] == 'HP21 8TR'

Now we can join `practice_postal` to `scripts`.

In [16]:
joined = scripts
for script in joined:
    script['post_code'] =practice_postal[script['practice']]
    print(practice_postal[script['practice']])

SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
S

SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
S

SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
S

SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
SK11 6JL
S

CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW
CW1 3AW


...

TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
TN34 1BA
T

KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
KT14 6DH
K

BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
B

BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
BH23 3AF
B

GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS
GU9 9QS


Finally we'll group the prescription dictionaries in `joined` by `'post_code'` and sum up the items prescribed in each group, as we did in the previous question.

In [3]:
import simplejson as json
with open('./joined.json', 'rb') as fp:
    joined = json.load(fp)

In [15]:
items_by_post = group_by_field(joined,('post_code',),['bnf_name'])

group_by_field
_json_to_data
_get_keys
_set_difference
_redundcy
_dic_unique_entry
_unique_entry
_index_dic
-dic_to_index


In [13]:
def sum_list(dicts):
    nl = {}
    for key in dicts.keys():
        nl[key] = sum([i[0] for i in dicts[key]])
    return nl

def unq_list(dicts):
    nl = {}
    for key in dicts.keys():
        nl[key] = [i[0] for i in dicts[key]]
    return nl

In [8]:
items_by_post = unq_list(items_by_post)


NameError: name 'unq_list' is not defined

In [ ]:
postal_totals = [('B11 4BW', 20673)] * 100

grader.score.pw__postal_totals(postal_totals)

## Question 4: items_by_region

Now we'll combine the techniques we've developed to answer a more complex question. Find the most commonly dispensed item in each postal code, representing the results as a list of tuples (`post_code`, `bnf_name`, amount dispensed as proportion of total). Sort your results ascending alphabetically by post code and take only results from the first 100 post codes.

**NOTE:** We'll continue to use the `joined` variable we created before, where we've chosen the alphabetically first postal code for each practice. Additionally, some postal codes will have multiple `'bnf_name'` with the same number of items prescribed for the maximum. In this case, we'll take the alphabetically first `'bnf_name'`.

In [ ]:
def new_dic(data,keys):
    new = {}
    for dic in data:
        n = {}
        for key in keys:
            n[key] = data[key]

            

In [17]:
def recursive(dic,fields):
    print("recursive")
    if len(fields) == 0:
        return dic
    else:
        key = fields[0]
        fields = fields[:1]
        dic = x()
        return(dic,fields)

def dictionary_out(dic,fields):
    for key in dic

In [21]:
"New Edited"


        
def _redundcy(data, fields):
    print("_redundcy")
    unique_dics_list = _dic_unique_entry(data, fields)
    groups = {}
    for f in fields:
        g = {}
        for e in unique_dics_list[f]:
            g[e] = _index_list(e, data[f])
        groups[f] = g
    return groups
    
def _index_list(item, my_list):
#    print("_index_list")
    """Return index list for a given key on list"""
    return [index for index, event in enumerate(my_list) if event == item ]

def _index_to_value(index_list,my_list):
#    print("_index_to_value")
    return [my_list[i] for i in index_list]

def _unique_entry(my_list):
    print("_unique_entry")
    return list(sorted(set(my_list)))

def _dic_unique_entry(data, fields):
    print("_dic_unique_entry")
    unq = {}
    for f in fields:
        unq[f] = _unique_entry(data[f])
    return unq
    
def _set_difference(data, fields):
    print("_set_difference")
    keys = set(data.keys())
    fields = set(fields)
    fields.add('index')
    d = keys.difference(fields)
    return d

def _get_keys(lst):
    print("_get_keys")
    return [key for key in lst[0].keys()] 
    
def _json_to_data(json):
    print("_json_to_data")
    data_dic = {}
    data_keys = _get_keys(json)
    """Make EMPTY LIST of Data Dictionary of each Keys"""
    for key in data_keys:
        data_dic[key] = []
    """Add All the Data to Specific key by opening each entry in First Loop & add on data_dic in next loop"""
    for entry in json:
        for key in data_keys:
            data_dic[key].append(entry[key]) 
    data_dic['index'] = list(range(0,len(data_dic[data_keys[0]])))
    return data_dic

def _index_dic(data,keys):
    print("_index_dic")
    i_dict = {}
    for i in data['index']:
        l = []
        for key in keys:
            l.append(data[key][i])
        i_dict[i] = l
    return i_dict

def _dic_to_index(groups,idx):
    print("-dic_to_index")
    ng = {}
    for f in groups.keys():
        for key in groups[f].keys():
            ng[key] = _index_to_value(groups[f][key],idx)
    return ng

def group_by_field(json, fields,k):
    print("group_by_field")
    data = _json_to_data(json)
    keys = list(_set_difference(data, fields))
    keys = k
    groups = _redundcy(data, fields)
    idx = _index_dic(data,keys)
    return _dic_to_index(groups,idx)

In [123]:

sample = joined
post_code = sorted(set([p['post_code'] for p in sample]))[:100]
print(len(post_code))

100


In [107]:
feild =[]
for f0 in feild:
    new ={}
    l = {}
    for d in sample:
        if d['post_code'] in post_code:
            if d['bnf_name'] in l.keys():
                l[d['bnf_name']] = l[d['bnf_name']] + d['items']
                print(d['post_code'])
            else:
                l.update({d['bnf_name'] : d['items']})
            print((d['post_code']))
            post_code
        else:
            new[d[f0]] = {}


In [148]:
l= {}
t = []
for i in post_code:
    x[i] = {}
    for d in sample:
        if d['post_code'] == i:
            if d['bnf_name'] in x.keys():
                x[d['bnf_name']] = l[d['bnf_name']] + d['items']
            else:
                x[i].update({d['bnf_name']: d['items']})
    l[i] = x[i]
    t.append(max_value(i,l[i]))

In [149]:
t

[('B11 4BW', 'Salbutamol_Inha 100mcg (200 D) CFF', 0.03885109599395314),
 ('B18 7AL', 'Amoxicillin_Cap 500mg', 0.03823018313059751),
 ('B21 9RY', 'Metformin HCl_Tab 500mg', 0.04046940118447028),
 ('B23 6DJ', 'Ventolin_Evohaler 100mcg (200 D)', 0.022113022113022112),
 ('B70 7AW', 'Omeprazole_Cap E/C 20mg', 0.019259576289321637),
 ('BB11 2DL', 'Omeprazole_Cap E/C 20mg', 0.02745930644019816),
 ('BB2 1AX', 'Omeprazole_Cap E/C 20mg', 0.029344432882414152),
 ('BB3 1PY', 'Omeprazole_Cap E/C 20mg', 0.029411764705882353),
 ('BB4 5SL', 'Omeprazole_Cap E/C 20mg', 0.029775167105529673),
 ('BB7 2JG', 'Omeprazole_Cap E/C 20mg', 0.028442002079310857),
 ('BB8 0JZ', 'Pneumococcal_Vac 0.5ml Vl (23 Valent)', 0.021108505122824344),
 ('BB9 7SR', 'Metformin HCl_Tab 500mg', 0.022995113538373097),
 ('BD3 8QH', 'Ramipril_Cap 10mg', 0.02284890901605599),
 ('BH18 8EE', 'Omeprazole_Cap E/C 20mg', 0.03806339612936411),
 ('BH23 3AF', 'Omeprazole_Cap E/C 20mg', 0.03895646042658205),
 ('BL1 8TU', 'Omeprazole_Cap E/C 

In [133]:
ls = []
for p in l:
    s = sum(l[p].values())
    print(p,s)
    for b in l[p]:
        if p == 'B11 4BW' and b == 'Salbutamol_Inha 100mcg (200 D) CFF':
            print(l[p][b]/s)
        ls.append(tuple([p,b,l[p][b]/s]))
('B11 4BW', 'Salbutamol_Inha 100mcg (200 D) CFF', 0.0341508247) in ls

B11 4BW 6615
0.03885109599395314
B18 7AL 7481
B21 9RY 9118
B23 6DJ 4477
B70 7AW 4673
BB11 2DL 7065
BB2 1AX 4805
BB3 1PY 7752
BB4 5SL 4937
BB7 2JG 26932
BB8 0JZ 8101
BB9 7SR 6958
BD3 8QH 4858
BH18 8EE 15553
BH23 3AF 11346
BL1 8TU 17847
BL3 5HP 4910
BL9 0NJ 5095
BL9 0SN 8310
CB9 8HF 22256
CH1 4DS 8404
CH65 6TG 8897
CT11 8AD 22643
CV1 4FS 4552
CW1 3AW 21078
CW5 5NX 7639
CW7 1AT 17578
DA1 2HA 6162
DA11 8BZ 10551
DN22 7XF 12455
DN34 4GB 5059
FY2 0JG 34841
FY4 1TJ 12685
FY5 2TZ 19190
FY7 8GU 4534
GL1 3PX 10226
GL50 4DP 13476
GU9 9QS 12444
HA0 4UZ 5052
HA3 7LT 4728
HG1 5AR 7856
HU7 4DW 8570
KT14 6DH 9985
KT6 6EZ 8270
L31 0DJ 7387
L36 7XY 5329
L5 0QW 6902
L7 6HD 13971
LA1 1PN 15387
LE10 1DS 10889
LE18 2EW 12409
LE5 3GH 4806
LN2 2JP 16079
LS9 9EF 18394
M11 4EJ 5696
M26 2SP 6401
M30 0NU 7817
M35 0AD 5945
ME8 8AA 10780
N9 7HD 6742
NE10 9QG 19997
NE24 1DX 10889
NE37 2PU 6369
NE38 7NQ 12415
NG7 3GW 3001
NG7 5HY 9167
NN16 8DN 11693
NW10 8RY 4569
OL1 1NL 5615
OL11 1DN 9552
OL4 1YN 7325
OL9 7AY 9129
P

False

In [135]:
ls =sorted(ls, key=lambda x: x[2])
ls[:100]

[('PL7 1AD', 'Gaviscon_Liq Orig Aniseed Relief', 2.3266094320746377e-05),
 ('PL7 1AD', 'Gaviscon Double Action_Tab Chble', 2.3266094320746377e-05),
 ('PL7 1AD', 'Zoton_FasTab Tab 15mg', 2.3266094320746377e-05),
 ('PL7 1AD', 'Asacol_MR Tab E/C 400mg', 2.3266094320746377e-05),
 ('PL7 1AD', 'Sulfasalazine_Oral Susp 250mg/5ml S/F', 2.3266094320746377e-05),
 ('PL7 1AD', 'Budesonide_Cap 3mg (E/C M/R Gran)', 2.3266094320746377e-05),
 ('PL7 1AD', 'Sod Cromoglicate_Cap 100mg', 2.3266094320746377e-05),
 ('PL7 1AD', 'Bisacodyl_Suppos 10mg', 2.3266094320746377e-05),
 ('PL7 1AD', 'Anusol Plus HC_Suppos', 2.3266094320746377e-05),
 ('PL7 1AD', 'Digoxin_Oral Soln Paed 50mcg/ml', 2.3266094320746377e-05),
 ('PL7 1AD', 'Frusol_Oral Soln 40mg/5ml S/F', 2.3266094320746377e-05),
 ('PL7 1AD', 'Amiloride HCl_Tab 5mg', 2.3266094320746377e-05),
 ('PL7 1AD', 'Co-Amilozide_Tab 5mg/50mg', 2.3266094320746377e-05),
 ('PL7 1AD', 'Tenormin L.S._Tab 50mg', 2.3266094320746377e-05),
 ('PL7 1AD', 'Labetalol HCl_Tab 100mg'

In [92]:
post_code_total = {}
for i in l.keys():
    post_code_total[i] = sum(l[i].values())
post_code_total

{'SK11 6JL': 57}

In [93]:
s= sum(post_code_total.values())
s

57

In [145]:
def max_value(i,dic):
    inverse = [(value, key) for key, value in dic.items()]
    return i,max(inverse)[1],max(inverse)[0]/sum(dic.values())


In [32]:
def recursive(data,feild):
    if len(feild) == 0:
        return data
    for f0 in feild:
    new ={}
    for d in sample:
        new[d[f0]] = {}
        print(d[])

SyntaxError: unexpected EOF while parsing (<ipython-input-32-9b6c3c860021>, line 2)

In [ ]:
d = {}
i = 0
for p in set(post_code):
    i += 1
    print(i)
    bnf_name = [b['bnf_name'] for b in sample if (b['post_code'] == p)]
    d[p] = {}
    for b in list(bnf_name):
        l = sum([i['items'] for i in sample if (i['post_code'] == p and i['bnf_name'] == b)])
        d[p][b] = l

1


In [ ]:
with open('data.json', 'w') as f:
    json.dump(d, f)

Now we need to calculate the total items of each `'bnf_name'` prescribed in each `'post_code'`. Use the techniques we developed in the previous questions to calculate these totals. You should have 141196 `('post_code', 'bnf_name')` groups.

In [22]:
"Items in bnf_name by post_code"
bnf_name_items = group_by_field(joined,('bnf_name',),['items'])

group_by_field
_json_to_data
_get_keys
_set_difference
_redundcy
_dic_unique_entry
_unique_entry
_index_dic


In [26]:
bnf_name_items[6]

[5]

In [42]:
b_sum = sum_list(bnf_name_items)
b_sum

{'3m Health Care_Cavilon Durable Barrier C': 1998,
 '3m Health Care_Cavilon No Sting 1ml Barr': 247,
 '3m Health Care_Cavilon No Sting 3ml Barr': 39,
 '3m Health Care_Cavilon No Sting Barrier': 350,
 'A.S Saliva Orthana Spy 50ml (App)': 25,
 'A2A Spacer': 46,
 'A2A Spacer + Sml/Med Mask': 36,
 'AMI_Suportx Ostomy & A/Support Ladies Br': 2,
 'AMI_Suportx Ostomy/Hernia Easy Peel Supp': 9,
 'APO-go PFS_Inf 5mg/ml 10ml Pfs': 2,
 'Abasaglar KwikPen_100u/ml 3ml Pf Pen': 97,
 'Abasaglar_100u/ml 3ml Cart': 5,
 'Abidec_Dps': 1233,
 'Able Spacer': 276,
 'Able Spacer + Sml/Med Mask': 77,
 'Abtard_Tab 10mg M/R': 2,
 'Abtard_Tab 20mg M/R': 8,
 'Acamprosate Calc_Tab E/C 333mg': 388,
 'Acarbose_Tab 100mg': 6,
 'Acarbose_Tab 50mg': 51,
 'Accrete D3_Tab': 5993,
 'Aceclofenac_Tab 100mg': 5,
 'Acemetacin_Cap 60mg': 5,
 'Acenocoumarol_Tab 1mg': 39,
 'Acetazolamide_Cap 250mg M/R': 44,
 'Acetazolamide_Tab 250mg': 182,
 'Acetic Acid_Ear Spy 2% 5ml': 256,
 'Acetylcy_Cap 600mg': 2,
 'Acetylcy_Eye Dps 5%': 26,


In [ ]:
total_items_by_bnf_post = group_by_field(joined,('post_code',),['bnf_name'])
assert len(total_items_by_bnf_post) == 141196

Let's use `total_items` to find the maximum item total for each postal code. To do this, we will want to regroup `total_items_by_bnf_post` by `'post_code'` only, not by `('post_code', 'bnf_name')`. First let's turn `total_items` into a list of dictionaries (similar to `scripts` or `practices`) and then group it by `'post_code'`. You should have 118 groups in the resulting `total_items_by_post` after grouping `total_items` by `'post_code'`.

In [ ]:
total_items = ...
assert len(total_items_by_post) == 118

Now we will aggregate the groups in `total_by_item_post` to create `max_item_by_post`. Some `'bnf_name'` have the same item total within a given postal code. Therefore, if more than one `'bnf_name'` has the maximum item total in a given postal code, we'll take the alphabetically first `'bnf_name'`. We can do this by [sorting](https://docs.python.org/2.7/howto/sorting.html) each group according to the item total and `'bnf_name'`.

In [ ]:
max_item_by_post = ...

In order to express the item totals as a proportion of the total amount of items prescribed across all `'bnf_name'` in a postal code, we'll need to use the total items prescribed that we previously calculated as `items_by_post`. Calculate the proportions for the most common `'bnf_names'` for each postal code. Format your answer as a list of tuples: `[(post_code, bnf_name, total)]`

In [ ]:
items_by_region = [('B11 4BW', 'Salbutamol_Inha 100mcg (200 D) CFF', 0.0341508247)] * 100

In [150]:
items_by_region = t

In [156]:
grader.score.pw__items_by_region(items_by_region)

Your score:  0.16


*Copyright &copy; 2017 The Data Incubator.  All rights reserved.*